In [1]:
import tensorflow as tf

import numpy as np
import os
import time

In [2]:
path_to_file = '../bible.txt'

In [3]:
text = open(path_to_file, 'rb').read().decode(encoding='utf-8')
# length of text is the number of characters in it
print('Length of text: {} characters'.format(len(text)))

Length of text: 4260254 characters


In [4]:
print(text[:500])

 Пятикнижие Моисея



 Бытие


 Глава 1

  1  В начале сотворил Бог небо и землю.
  2  Земля же была безвидна и пуста, и тьма над бездною, и Дух Божий носился над водою.
  3  И сказал Бог: да будет свет. И стал свет.
  4  И увидел Бог свет, что он хорош, и отделил Бог свет от тьмы.
  5  И назвал Бог свет днём, а тьму ночью. И был вечер, и было утро: день один.
  6  И сказал Бог: да будет твердь посреди воды, и да отделяет она воду от воды.
  7  И создал Бог твердь, и отделил воду,


In [5]:
text = text + text

In [6]:
# The unique characters in the file
vocab = sorted(set(text))
print('{} unique characters'.format(len(vocab)))

99 unique characters


In [7]:
# Creating a mapping from unique characters to indices
char2idx = {u:i for i, u in enumerate(vocab)}
idx2char = np.array(vocab)

text_as_int = np.array([char2idx[c] for c in text])

In [8]:
text_as_int, text, len(text_as_int), len(text)

(array([ 2, 49, 95, ...,  0,  1,  0]),
 ' Пятикнижие Моисея\r\n\r\n\r\n\r\n Бытие\r\n\r\n\r\n Глава 1\r\n\r\n  1 \xa0В начале сотворил Бог небо и землю.\r\n  2 \xa0Земля же была безвидна и пуста, и тьма над бездною, и Дух Божий носился над водою.\r\n  3 \xa0И сказал Бог: да будет свет. И стал свет.\r\n  4 \xa0И увидел Бог свет, что он хорош, и отделил Бог свет от тьмы.\r\n  5 \xa0И назвал Бог свет днём, а тьму ночью. И был вечер, и было утро: день один.\r\n  6 \xa0И сказал Бог: да будет твердь посреди воды, и да отделяет она воду от воды.\r\n  7 \xa0И создал Бог твердь, и отделил воду, которая под твердью, от воды, которая над твердью. И стало так.\r\n  8 \xa0И назвал Бог твердь небом. И был вечер, и было утро: день второй.\r\n  9 \xa0И сказал Бог: да соберётся вода, которая под небом, в одно место, и да явится суша. И стало так.\r\n  10 \xa0И назвал Бог сушу землёю, а собрание вод назвал морями. И увидел Бог, что [это] хорошо.\r\n  11 \xa0И сказал Бог: да произрастит земля зелень, тра

### train and target

In [9]:
# The maximum length sentence you want for a single input in characters
seq_length = 100
examples_per_epoch = len(text)//(seq_length+1)

# Create training examples / targets
char_dataset = tf.data.Dataset.from_tensor_slices(text_as_int)

for i in char_dataset.take(5):
    print(idx2char[i.numpy()])

 
П
я
т
и


In [10]:
sequences = char_dataset.batch(seq_length+1, drop_remainder=True)

for item in sequences.take(5):
    print(repr(''.join(idx2char[item.numpy()])))

' Пятикнижие Моисея\r\n\r\n\r\n\r\n Бытие\r\n\r\n\r\n Глава 1\r\n\r\n  1 \xa0В начале сотворил Бог небо и землю.\r\n  2 \xa0Земл'
'я же была безвидна и пуста, и тьма над бездною, и Дух Божий носился над водою.\r\n  3 \xa0И сказал Бог: да'
' будет свет. И стал свет.\r\n  4 \xa0И увидел Бог свет, что он хорош, и отделил Бог свет от тьмы.\r\n  5 \xa0И '
'назвал Бог свет днём, а тьму ночью. И был вечер, и было утро: день один.\r\n  6 \xa0И сказал Бог: да будет'
' твердь посреди воды, и да отделяет она воду от воды.\r\n  7 \xa0И создал Бог твердь, и отделил воду, кото'


In [11]:
def split_input_target(chunk):
    input_text = chunk[:-1]
    target_text = chunk[1:]
    return input_text, target_text

dataset = sequences.map(split_input_target)

Print the first example input and target values:

In [12]:
for input_example, target_example in  dataset.take(1):
    print('Input data: ', repr(''.join(idx2char[input_example.numpy()])))
    print('Target data:', repr(''.join(idx2char[target_example.numpy()])))

Input data:  ' Пятикнижие Моисея\r\n\r\n\r\n\r\n Бытие\r\n\r\n\r\n Глава 1\r\n\r\n  1 \xa0В начале сотворил Бог небо и землю.\r\n  2 \xa0Зем'
Target data: 'Пятикнижие Моисея\r\n\r\n\r\n\r\n Бытие\r\n\r\n\r\n Глава 1\r\n\r\n  1 \xa0В начале сотворил Бог небо и землю.\r\n  2 \xa0Земл'


In [13]:
# Batch size
BATCH_SIZE = 64

# Buffer size to shuffle the dataset
# (TF data is designed to work with possibly infinite sequences,
# so it doesn't attempt to shuffle the entire sequence in memory. Instead,
# it maintains a buffer in which it shuffles elements).
BUFFER_SIZE = 10000

dataset = dataset.shuffle(BUFFER_SIZE).batch(BATCH_SIZE, drop_remainder=True)

dataset

<BatchDataset shapes: ((64, 100), (64, 100)), types: (tf.int64, tf.int64)>

In [14]:
# Length of the vocabulary in chars
vocab_size = len(vocab)

# The embedding dimension
embedding_dim = 128

# Number of RNN units
rnn_units = 1024

In [15]:
model = tf.keras.Sequential(
    [
        tf.keras.layers.Embedding(vocab_size, embedding_dim),
        tf.keras.layers.LSTM(rnn_units, return_sequences=True),
        tf.keras.layers.Dense(vocab_size)
    ]
)

In [16]:
class RNNgenerator(tf.keras.Model):
    def __init__(self, vocab_size, embedding_dim, batch_size):
        super(RNNgenerator, self).__init__()
        
        self.emb = tf.keras.layers.Embedding(vocab_size, embedding_dim)
                                 
        self.gru1 = tf.keras.layers.GRU(rnn_units,
                            return_sequences=True,
                            recurrent_initializer='glorot_uniform')
        self.gru2 = tf.keras.layers.GRU(rnn_units,
                            return_sequences=True,
                            recurrent_initializer='glorot_uniform')
                           
        self.fc = tf.keras.layers.Dense(vocab_size)

    def call(self, x):
        emb_x = self.emb(x)
        x1 = self.gru1(emb_x)
        x = x1
        for _ in range(3):
            x = self.gru2(x)
        #x = self.gru1(x)
        x = (x + x1)/2
        return self.fc(x)

model = RNNgenerator(vocab_size, embedding_dim, BATCH_SIZE)

In [17]:
def build_model(vocab_size, embedding_dim, rnn_units, batch_size):
    model = tf.keras.Sequential([
        tf.keras.layers.Embedding(vocab_size, embedding_dim,
                                  batch_input_shape=[batch_size, None]),
                                 
        tf.keras.layers.LSTM(rnn_units,
                            return_sequences=True,
                            stateful=True,
                            recurrent_initializer='glorot_uniform'),

        tf.keras.layers.LSTM(rnn_units,
                            return_sequences=True,
                            stateful=True,
                            recurrent_initializer='glorot_uniform'),

         tf.keras.layers.LSTM(rnn_units,
                            return_sequences=True,
                            stateful=True,
                            recurrent_initializer='glorot_uniform'),
        
        tf.keras.layers.LSTM(rnn_units,
                            return_sequences=True,
                            stateful=True,
                            recurrent_initializer='glorot_uniform'),
                                   
        tf.keras.layers.Dense(vocab_size)
    ])
    return model

In [18]:
def build_model(vocab_size, embedding_dim, rnn_units, batch_size):
    model = tf.keras.Sequential([
        tf.keras.layers.Embedding(vocab_size, embedding_dim),
                                 
        tf.keras.layers.GRU(rnn_units,
                            return_sequences=True,
                            stateful=False,
                            recurrent_initializer='glorot_uniform'),

        tf.keras.layers.GRU(rnn_units,
                            return_sequences=True,
                            stateful=False,
                            recurrent_initializer='glorot_uniform'),

         tf.keras.layers.GRU(rnn_units,
                            return_sequences=True,
                            stateful=False,
                            recurrent_initializer='glorot_uniform'),
                                   
        tf.keras.layers.Dense(vocab_size)
    ])
    return model

In [19]:
model = build_model(
    vocab_size=len(vocab),
    embedding_dim=embedding_dim,
    rnn_units=rnn_units,
    batch_size=BATCH_SIZE)

In [20]:
for input_example_batch, target_example_batch in dataset.take(1):
    example_batch_predictions = model(input_example_batch)
    print(example_batch_predictions.shape, "# (batch_size, sequence_length, vocab_size)")

(64, 100, 99) # (batch_size, sequence_length, vocab_size)


In [21]:
model.summary()

Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_2 (Embedding)      (None, None, 128)         12672     
_________________________________________________________________
gru_2 (GRU)                  (None, None, 1024)        3545088   
_________________________________________________________________
gru_3 (GRU)                  (None, None, 1024)        6297600   
_________________________________________________________________
gru_4 (GRU)                  (None, None, 1024)        6297600   
_________________________________________________________________
dense_2 (Dense)              (None, None, 99)          101475    
Total params: 16,254,435
Trainable params: 16,254,435
Non-trainable params: 0
_________________________________________________________________


In [22]:
example_batch_predictions[0]

<tf.Tensor: shape=(100, 99), dtype=float32, numpy=
array([[-4.5444036e-04, -4.0367749e-04,  2.0417487e-04, ...,
         2.3788401e-04, -3.8063037e-04, -2.2687086e-04],
       [-3.1867088e-04, -1.0194890e-03,  5.8961037e-04, ...,
         2.9589579e-04, -1.2085816e-03, -3.9060600e-04],
       [-9.2234032e-04, -1.5440347e-03,  8.5808133e-04, ...,
        -2.5750895e-05, -9.2473795e-04, -1.1530204e-03],
       ...,
       [ 1.3724060e-03, -4.0368424e-03,  1.7582180e-03, ...,
        -4.3743388e-03,  2.0069296e-03, -2.5176292e-03],
       [ 1.8350612e-03, -5.0439071e-03,  1.5529328e-03, ...,
        -3.2871400e-03,  1.2415957e-03, -2.9208045e-03],
       [ 3.0624024e-03, -4.6141669e-03,  1.7186044e-03, ...,
        -1.5116259e-03,  4.2921468e-04, -3.4459815e-03]], dtype=float32)>

In [23]:
sampled_indices = tf.random.categorical(example_batch_predictions[0], num_samples=1)
sampled_indices = tf.squeeze(sampled_indices,axis=-1).numpy()

In [24]:
print("Input: \n", repr("".join(idx2char[input_example_batch[0]])))
print()
print("Next Char Predictions: \n", repr("".join(idx2char[sampled_indices ])))

Input: 
 'дений своих, и вы скоро погибнете с доброй земли, которую Господь даёт вам.\r\n  18 \xa0Итак положите сии'

Next Char Predictions: 
 'Э\xa0зД—И*б5СЯd?Юф!жЯ[ирТ68́ХcъМфШ4«МуОъв\rуЯЩГcЬащ,)ч)Г——ноъ40б9;аСPзЯ\n6ы?ьеСхЧёd8PЯ!«[с:зэБз.Ли\xa0Е!ёСЦ)'


## Train the model

In [25]:
def loss(labels, logits):
    return tf.keras.losses.sparse_categorical_crossentropy(labels, logits, from_logits=True)

example_batch_loss = loss(target_example_batch, example_batch_predictions)
print("Prediction shape: ", example_batch_predictions.shape, " # (batch_size, sequence_length, vocab_size)")
print("scalar_loss:      ", example_batch_loss.numpy().mean())

Prediction shape:  (64, 100, 99)  # (batch_size, sequence_length, vocab_size)
scalar_loss:       4.5945272


In [26]:
model.compile(optimizer='adam', loss=loss)

### Configure checkpoints

In [27]:
# Directory where the checkpoints will be saved
checkpoint_dir = './training_checkpoints'
# Name of the checkpoint files
checkpoint_prefix = os.path.join(checkpoint_dir, "ckpt_{epoch}")

checkpoint_callback = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_prefix,
    period=20,
    save_weights_only=True)

### Execute the training

In [28]:
EPOCHS = 20

In [29]:
history = model.fit(dataset, epochs=EPOCHS, callbacks=[checkpoint_callback])

Epoch 1/20
 873/1318 [==================>...........] - ETA: 32:30 - loss: 1.8486

KeyboardInterrupt: 

## Generate text

In [ ]:
tf.train.latest_checkpoint(checkpoint_dir)

'./training_checkpoints/ckpt_20'

In [ ]:
model = build_model(vocab_size, embedding_dim, rnn_units, batch_size=1)
model.load_weights(tf.train.latest_checkpoint(checkpoint_dir))
model.build(tf.TensorShape([1, None]))

In [ ]:
model.summary()

Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_1 (Embedding)      (1, None, 128)            16768     
_________________________________________________________________
lstm_4 (LSTM)                (1, None, 1024)           4722688   
_________________________________________________________________
lstm_5 (LSTM)                (1, None, 1024)           8392704   
_________________________________________________________________
lstm_6 (LSTM)                (1, None, 1024)           8392704   
_________________________________________________________________
lstm_7 (LSTM)                (1, None, 1024)           8392704   
_________________________________________________________________
dense_1 (Dense)              (1, None, 131)            134275    
Total params: 30,051,843
Trainable params: 30,051,843
Non-trainable params: 0
__________________________________________

In [ ]:
def generate_text(model, start_string):
    # Evaluation step (generating text using the learned model)

    # Number of characters to generate
    num_generate = 500

    # Converting our start string to numbers (vectorizing)
    input_eval = [char2idx[s] for s in start_string]
    input_eval = tf.expand_dims(input_eval, 0)

    # Empty string to store our results
    text_generated = []

    # Low temperature results in more predictable text.
    # Higher temperature results in more surprising text.
    # Experiment to find the best setting.
    temperature = 0.1

    # Here batch size == 1
    model.reset_states()
    for i in range(num_generate):
        predictions = model(input_eval)
        predictions = tf.squeeze(predictions, 0)
        # using a categorical distribution to predict the character returned by the model
        predictions = predictions / temperature
        predicted_id = tf.random.categorical(predictions, num_samples=1)[-1, 0].numpy()

        # Pass the predicted character as the next input to the model
        # along with the previous hidden state
        input_eval = tf.expand_dims([predicted_id], 0)

        text_generated.append(idx2char[predicted_id])

    return (start_string + ''.join(text_generated))

In [ ]:
text_ = generate_text(model, start_string=u"И вот идет уже ")
print(text_)

И вот идет уже стремятесь в том уверены,
                        Он слушал с солнцем обожатель
                        И в самом усталые слышать,
                        И вот оставляет на ночей,
                        И вот она во мверем он
                        И слышит голос и слезам.
                        Под ним подружился я в то время.
                                                                                                                                                                      
